In [1]:
import pandas as pd
import numpy as np
dataset_sin = pd.read_csv("export/dataset_without_resume.csv", delimiter=',', on_bad_lines='skip')
# imdb_resumes_bis.json
imdb_resumes = pd.read_json("export/imdb_resumes.json")


In [2]:
import re

for i in range(len(imdb_resumes)-1): # 
    print(i , '/', len(imdb_resumes))
    raw = imdb_resumes.iloc[i]

    values = [ raw['duree'], raw['genre'], raw['parental_advisor'] ]
    
    imdb_resumes.genre[i] = None
    imdb_resumes.duree[i] = None
    imdb_resumes.parental_advisor[i] = None

    for item in values:

        if type(item) is str :
            if '\n' in item:
                imdb_resumes.genre[i] = item
            elif 'min' in item:
                imdb_resumes.duree[i] = item
            else :
                imdb_resumes.parental_advisor[i] = item

0 / 299191
1 / 299191
2 / 299191
3 / 299191
4 / 299191
5 / 299191
6 / 299191
7 / 299191
8 / 299191
9 / 299191
10 / 299191
11 / 299191
12 / 299191
13 / 299191
14 / 299191
15 / 299191
16 / 299191
17 / 299191
18 / 299191
19 / 299191
20 / 299191
21 / 299191
22 / 299191
23 / 299191
24 / 299191
25 / 299191
26 / 299191
27 / 299191
28 / 299191
29 / 299191
30 / 299191
31 / 299191
32 / 299191
33 / 299191
34 / 299191
35 / 299191
36 / 299191
37 / 299191
38 / 299191
39 / 299191
40 / 299191
41 / 299191
42 / 299191
43 / 299191
44 / 299191
45 / 299191
46 / 299191
47 / 299191
48 / 299191
49 / 299191
50 / 299191
51 / 299191
52 / 299191
53 / 299191
54 / 299191
55 / 299191
56 / 299191
57 / 299191
58 / 299191
59 / 299191
60 / 299191
61 / 299191
62 / 299191
63 / 299191
64 / 299191
65 / 299191
66 / 299191
67 / 299191
68 / 299191
69 / 299191
70 / 299191
71 / 299191
72 / 299191
73 / 299191
74 / 299191
75 / 299191
76 / 299191
77 / 299191
78 / 299191
79 / 299191
80 / 299191
81 / 299191
82 / 299191
83 / 299191
84

In [3]:
imdb_resumes['duree'] = imdb_resumes['duree'].replace(r'\D+', '', regex=True)

imdb_resumes['genre'] = imdb_resumes['genre'].str.replace(r'\n', '')

imdb_resumes['resume'] = imdb_resumes['resume'].str.replace(r'\n', '')

imdb_resumes['duree'] = [ '0' if x == None else x for x in imdb_resumes['duree']]


<ipython-input-3-f2d1130583f2>:3: FutureWarning: The default value of regex will change from True to False in a future version.
  imdb_resumes['genre'] = imdb_resumes['genre'].str.replace(r'\n', '')
<ipython-input-3-f2d1130583f2>:5: FutureWarning: The default value of regex will change from True to False in a future version.
  imdb_resumes['resume'] = imdb_resumes['resume'].str.replace(r'\n', '')


In [4]:

imdb_resumes['duree'] = pd.to_numeric(imdb_resumes['duree'].astype(str).str.replace(',',''), errors='coerce').fillna(0).astype(int)

In [5]:

imdb_resumes['duree'] = [ np.nan if x == 0 else x for x in imdb_resumes['duree']]
imdb_resumes = imdb_resumes.dropna(subset=['duree'])

imdb_resumes = imdb_resumes.drop_duplicates(subset='imdb_search', keep="first")
imdb_resumes = imdb_resumes.reset_index().drop(columns=["index"])

In [6]:
import dask.dataframe as dd

dataset_sin = dd.from_pandas(dataset_sin, npartitions=10)
imdb_resumes = dd.from_pandas(imdb_resumes, npartitions=10)
print('1')
dataset = dataset_sin.merge(imdb_resumes, how="left", on=["imdb_search"])
print('2')
dataset = dataset.compute()
print('3')
dataset = dataset.drop(columns=['imdb_search','genre', 'numVotes'])


1
2
3


In [7]:
dataset.head()

originalTitle  startYear            genres  averageRating  \
0               Santera       1994             Drama            7.3   
1                 Maroa       2005     Music,Romance            6.5   
2  Hajde da se volimo 3       1990    Comedy,Musical            4.2   
3     Viola bacia tutti       1998  Adventure,Comedy            5.0   
4       Manuale d'am3re       2011    Comedy,Romance            5.9   

           primaryName parental_advisor  duree  \
0  Solveig Hoogesteijn             None   88.0   
1  Solveig Hoogesteijn        Not Rated  102.0   
2     Stanko Crnobrnja             None   92.0   
3    Giovanni Veronesi             None   93.0   
4    Giovanni Veronesi             None  125.0   

                                              resume  
0  About a mysterious and troubled black woman, a...  
1  An 11 year old petty criminal gets the chance ...  
2  The false story in the newspaper about the mar...  
3  Three friends leave for a trip by camper, but ...  
4  In Italy three men fall in love with three wom...

In [8]:
# Convert string Genre to list
dataset["genres"] = [ str(x).replace(' ', '') for x in dataset["genres"][:] ] 
dataset["genres"] = [ x.split(",") for x in dataset["genres"][:] ]


In [9]:
dataset["genres"].head()

0                [Drama]
1       [Music, Romance]
2      [Comedy, Musical]
3    [Adventure, Comedy]
4      [Comedy, Romance]
Name: genres, dtype: object

In [10]:
'''
# https://www.sbert.net/docs/quickstart.html#comparing-sentence-similarities
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('all-MiniLM-L6-v2')
# from unittest import result

dataset['genre'] = ''
dataset['themaScore'] = 0.0

for i in range( len(dataset) ):
    resume = dataset.iloc[i]['resume']
    genres = dataset.iloc[i]['genres']
    bestScore = 0.0
    bestGenre = ''
    for genre in genres:
        emb1 = model.encode(str(genre))
        emb2 = model.encode(str(resume))
        cos_sim = util.cos_sim(emb1, emb2)
        result = cos_sim.tolist()[0][0]
        if result > bestScore:
            bestScore = result
            bestGenre = genre
    # print(i, '/', len(dataset))
    dataset.themaScore[i] = bestScore
    dataset.genre[i] = bestGenre
    print(i,'/',len(dataset))
    
dataset = dataset.drop(columns=['genres'])
'''

"\n# https://www.sbert.net/docs/quickstart.html#comparing-sentence-similarities\nfrom sentence_transformers import SentenceTransformer, util\nmodel = SentenceTransformer('all-MiniLM-L6-v2')\n# from unittest import result\n\ndataset['genre'] = ''\ndataset['themaScore'] = 0.0\n\nfor i in range( len(dataset) ):\n    resume = dataset.iloc[i]['resume']\n    genres = dataset.iloc[i]['genres']\n    bestScore = 0.0\n    bestGenre = ''\n    for genre in genres:\n        emb1 = model.encode(str(genre))\n        emb2 = model.encode(str(resume))\n        cos_sim = util.cos_sim(emb1, emb2)\n        result = cos_sim.tolist()[0][0]\n        if result > bestScore:\n            bestScore = result\n            bestGenre = genre\n    # print(i, '/', len(dataset))\n    dataset.themaScore[i] = bestScore\n    dataset.genre[i] = bestGenre\n    print(i,'/',len(dataset))\n    \ndataset = dataset.drop(columns=['genres'])\n"

In [10]:
# https://www.youtube.com/watch?app=desktop&v=IEEhzQoKtQU&feature=youtu.be
# https://www.sbert.net/docs/quickstart.html#comparing-sentence-similarities
import threading
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('all-MiniLM-L6-v2')
# from unittest import result

dataset['genre'] = ''
dataset['themaScore'] = 0.0

def compute_themaScore(data):
    dataset = data
    for i in range( len(dataset) ):
        bestScore = 0.0
        bestGenre = ''
        for j in range(len(dataset.iloc[i]['genres'])-1):
            result = util.cos_sim(model.encode(str(dataset.iloc[i]['genres'][j])), model.encode(str(dataset.iloc[i]['resume']))).tolist()[0][0]
            if result > bestScore:
                bestScore = result
                bestGenre = dataset.iloc[i]['genres'][j]
        # print(i, '/', len(dataset))
        dataset.themaScore[i] = bestScore
        dataset.genre[i] = bestGenre
        print(i,'/',len(dataset))
    return dataset
'''
t1 = compute_themaScore(dataset[:30000])
t1 = dataset.drop(columns=['genres'])
t1.to_csv(r'temps/t1.csv', index = False, header=True)

t2 = compute_themaScore(dataset[30000:60000])
t2 = dataset.drop(columns=['genres'])
t2.to_csv(r'temps/t2.csv', index = False, header=True)

t3 = compute_themaScore(dataset[60000:90000])
t3 = dataset.drop(columns=['genres'])
t3.to_csv(r'temps/t3.csv', index = False, header=True)

t4 = compute_themaScore(dataset[90000:120000])
t4 = dataset.drop(columns=['genres'])
t4.to_csv(r'temps/t4.csv', index = False, header=True)

t5 = compute_themaScore(dataset[120000:150000])
t5 = dataset.drop(columns=['genres'])
t5.to_csv(r'temps/t5.csv', index = False, header=True)

t6 = compute_themaScore(dataset[150000:180000])
t6 = dataset.drop(columns=['genres'])
t6.to_csv(r'temps/t6.csv', index = False, header=True)
'''
'''
t7 = compute_themaScore(dataset[180000:210000])
t7 = dataset.drop(columns=['genres'])
t7.to_csv(r'temps/t7.csv', index = False, header=True)

t8 = compute_themaScore(dataset[210000:240000])
t8 = dataset.drop(columns=['genres'])
t8.to_csv(r'temps/t8.csv', index = False, header=True)

t9 = compute_themaScore(dataset[240000:270000])
t9 = dataset.drop(columns=['genres'])
t9.to_csv(r'temps/t9.csv', index = False, header=True)
'''
'''
t10 = compute_themaScore(dataset[270000:290000])
t10 = dataset.drop(columns=['genres'])
t10.to_csv(r'temps/t10.csv', index = False, header=True)
'''
t11 = compute_themaScore(dataset[290000:])
t11 = dataset.drop(columns=['genres'])
t11.to_csv(r'temps/t11.csv', index = False, header=True)


#dataset.to_csv(r'export/dataset.csv', index = False, header=True)
#dataset = dataset.drop(columns=['genres'])

In [5]:
dataset = pd.DataFrame()

for i in range(1,11):
    print(i, 'Start')
    importDF = pd.read_csv(f'temps/t{i}.csv', delimiter=',', on_bad_lines='skip')
    dataset = dataset.append(importDF)
    print(i, '...OK')

dataset.shape

1 Start


<ipython-input-5-9c9352cb3774>:5: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  importDF = pd.read_csv(f'temps/t{i}.csv', delimiter=',', on_bad_lines='skip')
<ipython-input-5-9c9352cb3774>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset = dataset.append(importDF)


1 ...OK
2 Start


<ipython-input-5-9c9352cb3774>:5: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  importDF = pd.read_csv(f'temps/t{i}.csv', delimiter=',', on_bad_lines='skip')
<ipython-input-5-9c9352cb3774>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset = dataset.append(importDF)


2 ...OK
3 Start


...

<ipython-input-5-9c9352cb3774>:5: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  importDF = pd.read_csv(f'temps/t{i}.csv', delimiter=',', on_bad_lines='skip')
<ipython-input-5-9c9352cb3774>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset = dataset.append(importDF)


9 ...OK
10 Start


<ipython-input-5-9c9352cb3774>:5: DtypeWarning: Columns (7) have mixed types. Specify dtype option on import or set low_memory=False.
  importDF = pd.read_csv(f'temps/t{i}.csv', delimiter=',', on_bad_lines='skip')
<ipython-input-5-9c9352cb3774>:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset = dataset.append(importDF)


10 ...OK


(3042340, 9)

In [ ]:
'''
# https://www.youtube.com/watch?app=desktop&v=IEEhzQoKtQU&feature=youtu.be
# https://www.sbert.net/docs/quickstart.html#comparing-sentence-similarities
import threading
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('all-MiniLM-L6-v2')
# from unittest import result

dataset['genre'] = ''
dataset['themaScore'] = 0.0

def compute_themaScore(data):
    dataset = data
    for i in range( len(dataset) ):
        bestScore = 0.0
        bestGenre = ''
        for j in range(len(dataset.iloc[i]['genres'])-1):
            result = util.cos_sim(model.encode(str(dataset.iloc[i]['genres'][j])), model.encode(str(dataset.iloc[i]['resume']))).tolist()[0][0]
            if result > bestScore:
                bestScore = result
                bestGenre = dataset.iloc[i]['genres'][j]
        # print(i, '/', len(dataset))
        dataset.themaScore[i] = bestScore
        dataset.genre[i] = bestGenre
        print(i,'/',len(dataset))
    return dataset

import concurrent.futures

with concurrent.futures.ThreadPoolExecutor() as executor:
    future = executor.submit(compute_themaScore, dataset)
    return_value = future.result()
    dataset2 = return_value
    
dataset2 = dataset2.drop(columns=['genres'])
'''

In [6]:
dataset = dataset.rename(columns={"originalTitle": "title", "startYear": "year", "primaryName" : "director", "parental_advisor" : "parentalAdvisor", "averageRating" : "imdbRating"})

In [7]:
dataset.to_csv(r'export/dataset.csv', index = False, header=True)